# Measuring Thanksgiving-dinner inflation

Thanksgiving is a time to reflect on all the reasons to be grateful. You might be grateful that your live in a world of smartphones and antibiotics. You might be grateful that Gibralter rock is only a short drive from Madison. You might be grateful for your friends and your family. Maybe you are grateful for your econ instructors...

Thanksgiving is also a time to gather for a meal. It doesn't really matter what you are eating as long as you are doing it with others in the spirit of giving thanks. The traditional American Thanksgiving meal, though, includes turkey, stuffing, potatoes, vegetables, cheese (at least, it does in Wisconsin) and maybe some wine to wash it all down.

How much has the cost of Thanksgiving dinner changed over the years? If dinner for four cost $50 in 2015, what would it cost today? Which components of dinner have seen the largest price changes?

Let's figure this out by computing a fixed-weight price index, like the cpi. We need prices and expenditure weights. The change in the price of dinner (the Thanksgiving-dinner inflation rate) is


$$\pi_t^{\text{Dinner}} = \pi_t^{\text{Turkey}}\times \omega^{\text{Turkey}}+\pi_t^{\text{Bread}}\times \omega^{\text{Bread}}+\cdots,$$

where the $\omega$ are the fixed expenditure weights that sum to one. The expenditure weights are determined in a base period and held constant over time. By introspection, I've determined the weights in a Thanksgiving dinner to be
```python
exp_weights = {'turkey':0.3, 'bread':0.07, 'butter':0.03, 'potatoes':0.15, 'wine':0.23, 'cheese':0.12, 'vegetables':0.1},
```
which means 30 percent of the cost of dinner is the turkey, 7 percent is bread, etc.

We have weights, so now we just need the inflation rates of the components. Let's use the data from the Bureau of Labor Statistics [cpi databases](https://www.bls.gov/cpi/data.htm). These are the "all urban consumers" series. You could use the online access to download a bunch of csv files, but we know how to work with apis, so let's approach this like the pros do. I've already dug out the codes for each variable.

## An aside on price indexes

There are different types of price indexes out there, including fixed-weight and fixed-price indexes and the chained Fisher index used at the Bureau of Economic Analysis. We have to choose one. Our fixed-weight index is similar to the cpi.

An issue with fixed-weight price indexes is [substitution bias](https://www.bls.gov/opub/btn/volume-1/consumer-price-index-data-quality-how-accurate-is-the-us-cpi.htm). Goods that become relatively more expensive could find their expenditure shares falling (if goods are substitutes), so our fixed shares would overstate inflation. Unfortunately, there is not a perfect price index that is easy to compute, so we do the best we can, just like they do with the cpi.  


## 1. Get the data

We are going to use the BLS api to retrieve the price indexes. This way, when you want to update your work next year to include the most recent data, all you will need to do is re-run the notebook. Nice.

I started with the [BLS api docs](https://www.bls.gov/developers/) and the [sample code in python](https://www.bls.gov/developers/api_python.htm).

1. Retrieve data for 2015&ndash;2023. The code for each good is in the dictionary below.

```python
dinner = {'CUSR0000SEFF02':'turkey', 'CUSR0000SEFB01':'bread', 'CUSR0000SS10011':'butter', 'CUSR0000SEFL01':'potatoes',
           'CUSR0000SEFW03':'wine',  'CUSR0000SEFJ02':'cheese', 'CUSR0000SEFL04':'vegetables'}
           ```

Once you have downloaded the data, you have a json object. This is basically nested dictionaries and lists to be sorted through. I wrestled with this for awhile, but it's doable. You can do it, too.

2. Create a DataFrame with time as rows and the price indexes for each good as columns.

## 2. Compute inflation

Now that we have the data, let's compute the inflation rate. The inflation rate is just the growth rate of the price indexes.

1. Compute the year-over-year growth rate of each price index.

2. Now compute the Thanksgiving dinner price index. In each year, compute the weighted sum of the inflation rates, where $\pi$ are the inflation rates and $\omega$ are the expenditure weights. Notice that the $\pi$ change over time, but the weights do not.

$$\pi_t^{\text{Dinner}} = \pi_t^{\text{Turkey}}\times \omega^{\text{Turkey}}+\pi_t^{\text{Bread}}\times \omega^{\text{Bread}}+\cdots$$


The weights are
```python
exp_weights = {'turkey':0.3, 'bread':0.07, 'butter':0.03, 'potatoes':0.15, 'wine':0.23, 'cheese':0.12, 'vegetables':0.1}
```

3. Plot your Thanksgiving dinner inflation rate. I didn't do it, but you could add the overall cpi or the cpi for food to see how it compares to Thanksgiving.

## 3. Compute cumulative inflation

How much did inflation change over the whole period? Let's compute cumulative inflation.

1. We computed year-over-year inflation rates (an annual rate), so we should only use one observation from each year. Let's use October. Create a DataFrame that only has the October observation from each year.
2. Add 1 to each growth rate. If you multiplied your growth rates by 100, divide them by 100 before adding 1.
3. Compute the cumulative product of each column.
4. Set the 2015 row (which is NA) to be ones.   

The last row of the DataFrame will be one plus the cumulative growth rate.

## 4. So how much more is that?

Suppose dinner for a family of four was $50 in 2015. What does that dinner cost in 2023?

## 5. What goods drove the increase in prices?

Why is Thanksgiving dinner 61 percent more expensive than it was in 2015? Which parts of dinner had the largest price increases?

1. Create a bar plot with the cumulative inflation rates for each of the components of dinner, in October 2023.

2. You could continue your analysis by plotting the contributions of each component. For example, butter has a high inflation rate, but its weight is only three percent. I'll leave that for you to experiment with!  